In [ ]:
# Step 1: Mount Google Drive
from google.colab import drive
drive.mount('/content/drive')

##Aesthetic sorting using CLIP

In [ ]:
# --------------------------------------------------------------
# 0. INSTALL & MOUNT
# --------------------------------------------------------------
!pip install -q open_clip_torch torch torchvision pillow tqdm pandas ftfy regex scikit-learn

import zipfile, os, shutil, tempfile, requests, numpy as np
from tqdm import tqdm
import torch, open_clip
from PIL import Image
import glob, pandas as pd
from sklearn.metrics.pairwise import cosine_similarity
from google.colab import drive

drive.mount('/content/drive')

In [ ]:
# --------------------------------------------------------------
# 1. PARAMETERS  (Google-Colab Form UI)
# --------------------------------------------------------------

#@title **Input Settings** { display-mode: "form" }

ZIP_PATH = "/content/drive/MyDrive/training_data_31635.zip" #@param {type:"string"}
EXTRACT_TO = "/content/hellsing_aesthetic_sorted" #@param {type:"string"}
OUT_DIR = "/content/drive/MyDrive/hellsing_aesthetic_sorted" #@param {type:"string"}

#@title **Deduplication Settings** { display-mode: "form" }

SIMILARITY_THRESHOLD = 0.99 #@param {type:"slider", min:0.9, max:1.0, step:0.005}
FILESIZE_TOLERANCE    = 0.05 #@param {type:"slider", min:0.0, max:0.2, step:0.01}

#@title **Packing Settings** { display-mode: "form" }

MAX_ZIP_BYTES = 300 #@param {type:"slider", min:50, max:1000, step:50}
MAX_ZIP_BYTES = MAX_ZIP_BYTES * 1024 * 1024   # convert MiB → bytes

# -----------------------------------------------------------------
# (no changes needed below – the rest of the notebook uses these vars)
# -----------------------------------------------------------------
os.makedirs(EXTRACT_TO, exist_ok=True)
os.makedirs(OUT_DIR,    exist_ok=True)

print("Parameters loaded from the form")

In [ ]:
# --------------------------------------------------------------
# 2. EXTRACT ONLY IMAGES (skip if already done)
# --------------------------------------------------------------
if not os.listdir(EXTRACT_TO):
    with zipfile.ZipFile(ZIP_PATH, 'r') as z:
        members = [m for m in z.namelist()
                   if m.lower().split('.')[-1] in {'png','jpg','jpeg','bmp','webp'}]
        for member in tqdm(members, desc='Extracting images'):
            z.extract(member, EXTRACT_TO)
else:
    print("Folder already contains files – skipping extraction.")

In [ ]:
# --------------------------------------------------------------
# 3. LOAD CLIP + AESTHETIC HEAD
# --------------------------------------------------------------
device = "cuda" if torch.cuda.is_available() else "cpu"

clip_model, _, preprocess = open_clip.create_model_and_transforms(
    model_name="ViT-B-32", pretrained="laion400m_e32"
)
clip_model.to(device).eval()

# ---- aesthetic head ------------------------------------------------
AESTHETIC_URL = "https://github.com/LAION-AI/aesthetic-predictor/raw/main/sa_0_4_vit_b_32_linear.pth"
ckpt_path = "/content/laion_aesthetic_vit_b_32.pth"
if not os.path.exists(ckpt_path):
    print("Downloading aesthetic weights …")
    r = requests.get(AESTHETIC_URL); r.raise_for_status()
    open(ckpt_path, 'wb').write(r.content)

aesthetic_head = torch.nn.Linear(512, 1).to(device)
aesthetic_head.load_state_dict(torch.load(ckpt_path, map_location=device))
aesthetic_head.eval()
print("CLIP + aesthetic head ready")

In [ ]:
# --------------------------------------------------------------
# 4. SCORE ALL IMAGES
# --------------------------------------------------------------
image_paths = glob.glob(f"{EXTRACT_TO}/**/*.*", recursive=True)
image_paths = [p for p in image_paths
               if p.lower().split('.')[-1] in {'png','jpg','jpeg','bmp','webp'}]

results = []
with torch.no_grad():
    for p in tqdm(image_paths, desc="Scoring"):
        try:
            img = Image.open(p).convert("RGB")
            x   = preprocess(img).unsqueeze(0).to(device)
            emb = clip_model.encode_image(x)               # (1,512)

            logit = aesthetic_head(emb)
            score = torch.sigmoid(logit).item() * 10.0     # 0-10 scale

            results.append({'path': p, 'score': score})
        except Exception as e:
            print(f"Skip {p}: {e}")

df = pd.DataFrame(results)
df = df.sort_values('score', ascending=False).reset_index(drop=True)
print(f"Scored {len(df)} images | best {df['score'].iloc[0]:.2f} | worst {df['score'].iloc[-1]:.2f}")

In [ ]:
# --------------------------------------------------------------
# 5. DEDUPLICATION (file-size + CLIP similarity)
# --------------------------------------------------------------
@torch.no_grad()
def get_clip_embedding(p):
    try:
        img = Image.open(p).convert("RGB")
        x   = preprocess(img).unsqueeze(0).to(device)
        emb = clip_model.encode_image(x)
        emb = emb / emb.norm(dim=-1, keepdim=True)
        return emb.cpu().numpy().flatten()
    except Exception:
        return None

# ---- group by approximate size ------------------------------------
size_groups = {}
for p in df['path']:
    sz = os.path.getsize(p)
    key = round(sz * (1 / (1 + FILESIZE_TOLERANCE)))
    size_groups.setdefault(key, []).append(p)

kept_paths = []
for key, group in tqdm(size_groups.items(), desc="Deduplicate groups"):
    if len(group) == 1:
        kept_paths.append(group[0])
        continue

    # compute embeddings only for this small group
    embeddings = []
    valid_paths = []
    for p in group:
        emb = get_clip_embedding(p)
        if emb is not None:
            embeddings.append(emb)
            valid_paths.append(p)

    if len(embeddings) <= 1:
        kept_paths.extend(valid_paths)
        continue

    embeddings = np.stack(embeddings)
    sim = cosine_similarity(embeddings)

    keep = [True] * len(valid_paths)
    for i in range(len(valid_paths)):
        if not keep[i]: continue
        for j in range(i+1, len(valid_paths)):
            if sim[i, j] >= SIMILARITY_THRESHOLD:
                keep[j] = False

    for idx, k in enumerate(keep):
        if k:
            kept_paths.append(valid_paths[idx])

# ---- filter original dataframe ------------------------------------
df_clean = df[df['path'].isin(kept_paths)].copy()
df_clean = df_clean.sort_values('score', ascending=False).reset_index(drop=True)
print(f"After deduplication: {len(df_clean)} images (removed {len(df)-len(df_clean)} duplicates)")

In [ ]:
# --------------------------------------------------------------
# 6. PACK CLEANED IMAGES INTO ≤300 MiB ZIPs
# --------------------------------------------------------------
temp_dir = '/content/zip_temp'
os.makedirs(temp_dir, exist_ok=True)

current_files = []      # (temp_path, arcname)
current_size  = 0
zip_idx       = 1

def finish_zip():
    global zip_idx, current_size, current_files
    if not current_files: return
    zip_path = f"{OUT_DIR}/mia_panels_part_{zip_idx:03d}.zip"
    with zipfile.ZipFile(zip_path, 'w', zipfile.ZIP_DEFLATED) as z:
        for src, arc in current_files:
            z.write(src, arc)
    mb = os.path.getsize(zip_path) / 1e6
    print(f"Saved {zip_path}  ({len(current_files)} files, {mb:.1f} MB)")
    for src, _ in current_files:
        os.remove(src)
    current_files = []
    current_size = 0
    zip_idx += 1

for idx, row in enumerate(tqdm(df_clean.itertuples(), total=len(df_clean), desc="Packing")):
    src  = row.path
    rank = idx + 1
    ext  = os.path.splitext(src)[1].lower()
    tmp  = f"{temp_dir}/{rank}{ext}"
    shutil.copyfile(src, tmp)

    fsize = os.path.getsize(tmp)
    if current_size + fsize > MAX_ZIP_BYTES and current_files:
        finish_zip()

    current_files.append((tmp, f"{rank}{ext}"))
    current_size += fsize

finish_zip()
shutil.rmtree(temp_dir, ignore_errors=True)

# --------------------------------------------------------------
# 7. SAVE SCORE CSV (only the kept images)
# --------------------------------------------------------------
df_clean.to_csv(f"{OUT_DIR}/aesthetic_scores_clean.csv", index=False)
print("\nAll done! Cleaned ZIPs + CSV are in:", OUT_DIR)

##Sort images into folders using CLIP image feature extraction

In [ ]:
#@markdown Unzip training data from drive to /content/ (if required)
path = '/content/drive/MyDrive/training_data_66708.zip' #@param {type:'string'}

%cd /content/
!unzip  {path}

In [ ]:
!pip install ftfy regex tqdm
!pip install git+https://github.com/openai/CLIP.git
!pip install scikit-learn matplotlib pillow umap-learn  # UMAP is optional for 2D visualization

Load Images and Extract CLIP Embeddings

Upload your images the normal way ( `/content/`) prior to running this cell.

This code loads all images (supports JPG, PNG, etc.), preprocesses them, and extracts 512-dimensional embeddings using the ViT-B/32 CLIP model.

In [ ]:
!pip install open_clip_torch

import os
import numpy as np
import torch
import open_clip
from PIL import Image

# Configuration
image_dir = '/content/'  #@param {type:'string'}
device = "cuda" if torch.cuda.is_available() else "cpu"
model_name = "ViT-B-32"  # Available per error message
pretrained = "laion400m_e32"  # Robust pretrained weights

# Load OpenCLIP model
model, _, preprocess = open_clip.create_model_and_transforms(model_name, pretrained=pretrained)
model.to(device)
model.eval()

# Load images and extract embeddings
embeddings = []
image_paths = []
image_names = []

# Recursively find images in subdirectories, excluding /content/drive/
for root, _, files in os.walk(image_dir):
    if '/drive/' in root:  # Explicitly skip any directory containing '/drive/'
        continue
    for filename in files:
        if filename.lower().endswith(('.png', '.jpg', '.jpeg', '.gif', '.bmp')):
            img_path = os.path.join(root, filename)
            try:
                image = preprocess(Image.open(img_path)).unsqueeze(0).to(device)
                with torch.no_grad():
                    embedding = model.encode_image(image)
                embeddings.append(embedding.cpu().numpy().flatten())
                image_paths.append(img_path)
                image_names.append(filename)
                #print(f"Processed: {filename}")
            except Exception as e:
                print(f"Error processing {filename}: {e}")

embeddings = np.array(embeddings)
print(f"Extracted embeddings for {len(embeddings)} images. Shape: {embeddings.shape}")

Perform Clustering
We'll use K-Means clustering on the embeddings. You can choose the number of clusters (`n_clusters`) based on your dataset size (e.g., try 5-10). We'll also compute the silhouette score to evaluate cluster quality (higher is better).

For visualization, we'll optionally reduce dimensions to 2D using UMAP.

In [ ]:
from umap import UMAP  # For 2D projection (optional)
import os
import numpy as np
import torch
import clip
from PIL import Image
import matplotlib.pyplot as plt
from sklearn.cluster import KMeans
from sklearn.metrics import silhouette_score
import warnings
warnings.filterwarnings('ignore')
#@markdown Choose number of clusters (experiment with this)
n_clusters = 100  # @param {type:'slider' , min:1 , max:200, step:1}

# Perform K-Means clustering
kmeans = KMeans(n_clusters=n_clusters, random_state=42, n_init=10)
cluster_labels = kmeans.fit_predict(embeddings)

# Evaluate clustering quality
sil_score = silhouette_score(embeddings, cluster_labels)
print(f"Silhouette Score: {sil_score:.3f} (closer to 1 is better)")

# Optional: 2D visualization with UMAP
reducer = UMAP(random_state=42, n_components=2)
embed_2d = reducer.fit_transform(embeddings)

plt.figure(figsize=(10, 8))
scatter = plt.scatter(embed_2d[:, 0], embed_2d[:, 1], c=cluster_labels, cmap='tab10', s=50)
plt.colorbar(scatter)
plt.title(f'2D UMAP Projection of CLIP Embeddings (K={n_clusters} Clusters)')
plt.xlabel('UMAP 1')
plt.ylabel('UMAP 2')
plt.show()

In [ ]:
import shutil
import os
from PIL import Image

# Create output directories
output_dir = '/content/clusters'  # Output base directory
os.makedirs(output_dir, exist_ok=True)

move_files = False  # Set to True to move files, False to copy

# Create directories for each cluster
for i in range(n_clusters):
    cluster_dir = os.path.join(output_dir, f'cluster_{i}')
    os.makedirs(cluster_dir, exist_ok=True)

# Form inputs using Colab's # @param
output_format = "JPEG"  # @param ["JPEG", "PNG", "WEBP"]
quality = 100  # @param {type:"slider", min:0, max:100, step:1}

# Function to convert and save images
for idx, label in enumerate(cluster_labels):
    src_path = image_paths[idx]  # Use full path
    # Create destination filename with selected extension
    dst_filename = os.path.splitext(image_names[idx])[0] + f'.{output_format.lower()}'
    dst_path = os.path.join(output_dir, f'cluster_{label}', dst_filename)

    try:
        # Open and convert image
        with Image.open(src_path).convert('RGB') as img:
            if output_format == 'JPEG':
                img.save(dst_path, 'JPEG', quality=quality, optimize=True)
            elif output_format == 'PNG':
                # PNG compression: 0 (max compression) to 9 (no compression)
                # Map quality 0-100 to PNG compression 9-0
                png_compression = int(9 - (quality / 100 * 9))
                img.save(dst_path, 'PNG', compress_level=png_compression)
            elif output_format == 'WEBP':
                img.save(dst_path, 'WEBP', quality=quality)

            if move_files:
                os.remove(src_path)  # Delete original if moving
            print(f"Assigned {image_names[idx]} as {dst_filename} to cluster_{label}")
    except Exception as e:
        print(f"Error converting {image_names[idx]} to {output_format}: {e}")

print(f"Images sorted into {n_clusters} clusters in '{output_dir}' as .{output_format.lower()}")

In [ ]:
from PIL import Image
import matplotlib.pyplot as plt
import os

def display_cluster_samples(cluster_dir, n_samples=3):
    # Check if cluster directory exists
    if not os.path.exists(cluster_dir):
        print(f"Cluster directory {cluster_dir} does not exist")
        return

    # Updated to include .jpg, .png, and .webp files
    images = [f for f in os.listdir(cluster_dir) if f.lower().endswith(('.jpg', '.jpeg', '.png', '.webp'))][:n_samples]
    if not images:
        print(f"No images in {cluster_dir}")
        return

    fig, axs = plt.subplots(1, len(images), figsize=(5 * len(images), 5))
    if len(images) == 1:
        axs = [axs]
    for j, img_file in enumerate(images):
        img_path = os.path.join(cluster_dir, img_file)
        try:
            img = Image.open(img_path).convert('RGB')  # Ensure RGB for display
            axs[j].imshow(img)
            axs[j].set_title(img_file)
            axs[j].axis('off')
        except Exception as e:
            print(f"Error displaying {img_file}: {e}")
    plt.show()

# Create output directories
output_dir = '/content/clusters'  # Output base directory

# Check if output directory exists
if not os.path.exists(output_dir):
    print(f"Output directory {output_dir} does not exist")
else:
    # Display samples from each cluster
    for i in range(n_clusters):  # Ensure n_clusters is defined
        cluster_dir = os.path.join(output_dir, f'cluster_{i}')
        print(f"\nSamples from Cluster {i}:")
        display_cluster_samples(cluster_dir)

In [ ]:
import shutil
%cd /content/
#@markdown Remove cluster_N.  You can set multiple indices at once 1,4,5,9,...
nums ='1,5,9,12,16,18,20,22,31,33,34,36,37,38,53,58,60,62,66,71,74,79,85,87,88,92,93,95,98'#@param {type:'string'}

for num in nums.split(','):
  if num.strip() == '': continue
  shutil.rmtree(f'/content/clusters/cluster_{num.strip()}')

/content


Sort Images into Clusters
This creates subdirectories for each cluster and moves/copies the images there. Set `move_files=True` to move (or False to copy).

Visualize Sample Images per Cluster
Display a few sample images from each cluster to inspect the results.

In [ ]:
#@markdown Upload to Google Drive as .zip folder (Be mindful of Google Drive Terms of Service)
drive_folder_name = 'hellsing_clusters' # @param {type:'string'}

%cd /content/
!zip -r /content/drive/MyDrive/{drive_folder_name}.zip {output_dir}



##Comic/Manga Panel Extract from images using Deep Panel trained model

https://huggingface.co/datasets/codeShare/lora-training-data/tree/main/Made%20In%20Abyss

Step 2:  Do mangapanel sorting. You need to download the keras model off the hf repo for this :

In [ ]:
# Cell 1: Unzip the new dataset
#@markdown Unzip training data from drive to /content/ (if required)
path = '/content/drive/MyDrive/hellsing_clusters.zip' #@param {type:'string'}

%cd /content/
!unzip {path}

# Cell 2: Setup and panel extraction
# Install required dependencies
!pip install tensorflow
!pip install opencv-python-headless
!pip install numpy
!pip install tqdm
!pip install datasets  # For Hugging Face dataset

# Clone the DeepPanel repository (for any required utilities)
!git clone https://github.com/pedrovgs/DeepPanel.git
%cd DeepPanel

# Import necessary libraries
import os
import cv2
import numpy as np
import tensorflow as tf
from tqdm import tqdm
from google.colab import drive
from datasets import Dataset
import pandas as pd
import zipfile

# Mount Google Drive
drive.mount('/content/drive')

# Verify dataset structure
!ls /content/content
!ls /content/content/clusters
# Verify a sample cluster (uncomment if needed for debugging)
# !ls /content/content/clusters/cluster_1

# Define paths
model_path = '/content/drive/MyDrive/deeppanel_model.keras'  # Updated to .keras
clusters_path = '/content/content/clusters'
output_dir = '/content/extracted_panels'
zip_output_path = '/content/extracted_panels.zip'

# Create output directory
os.makedirs(output_dir, exist_ok=True)

# Load the trained model
model = tf.keras.models.load_model(model_path)

# Function to preprocess image for model input
def preprocess_image(image_path, target_size=(256, 256)):
    image = cv2.imread(image_path)
    if image is None:
        raise ValueError(f"Failed to load image: {image_path}")
    image = cv2.cvtColor(image, cv2.COLOR_BGR2RGB)
    original_shape = image.shape[:2]
    image = cv2.resize(image, target_size)
    image = image / 255.0  # Normalize to [0, 1]
    return image, original_shape

# Function to post-process mask and extract panels
def extract_panels(image_path, mask, original_shape, output_dir, cluster_name, image_idx):
    # Resize mask to original image size
    mask = cv2.resize(mask, (original_shape[1], original_shape[0]), interpolation=cv2.INTER_NEAREST)
    mask = (mask > 0.5).astype(np.uint8) * 255  # Threshold to binary mask

    # Find contours
    contours, _ = cv2.findContours(mask, cv2.RETR_EXTERNAL, cv2.CHAIN_APPROX_SIMPLE)

    # Load original image for cropping
    original_image = cv2.imread(image_path)
    if original_image is None:
        raise ValueError(f"Failed to load original image: {image_path}")

    # Create output directory for this cluster
    cluster_output_dir = os.path.join(output_dir, cluster_name)
    os.makedirs(cluster_output_dir, exist_ok=True)

    # Extract panels
    for i, contour in enumerate(contours):
        # Get bounding box for each contour
        x, y, w, h = cv2.boundingRect(contour)
        # Skip small contours (optional, adjust threshold as needed)
        if w * h < 1000:  # Ignore small regions (e.g., noise)
            continue
        # Crop panel from original image
        panel = original_image[y:y+h, x:x+w]
        # Save panel
        panel_path = os.path.join(cluster_output_dir, f'panel_{image_idx}_{i}.jpg')
        cv2.imwrite(panel_path, panel)

# Option 1: Process images directly (if dataset is small)
def process_images_directly(clusters_path, model, output_dir):
    cluster_folders = [f for f in os.listdir(clusters_path) if f.startswith('cluster_')]

    for cluster_name in tqdm(cluster_folders, desc="Processing clusters"):
        cluster_path = os.path.join(clusters_path, cluster_name)
        image_files = [f for f in os.listdir(cluster_path) if f.endswith(('.jpg', '.jpeg'))]

        for idx, image_file in enumerate(tqdm(image_files, desc=f"Processing {cluster_name}")):
            image_path = os.path.join(cluster_path, image_file)
            try:
                # Preprocess image
                image, original_shape = preprocess_image(image_path)
                # Predict mask
                mask = model.predict(np.expand_dims(image, axis=0), verbose=0)[0]
                if mask.shape[-1] > 1:  # Handle multi-class masks
                    mask = np.argmax(mask, axis=-1)  # Convert to single-channel
                else:
                    mask = mask[..., 0]  # Binary mask
                # Extract and save panels
                extract_panels(image_path, mask, original_shape, output_dir, cluster_name, idx)
            except Exception as e:
                print(f"Error processing {image_path}: {e}")

# Option 2: Create Hugging Face dataset (for large datasets)
def create_hf_dataset(clusters_path):
    data = []
    cluster_folders = [f for f in os.listdir(clusters_path) if f.startswith('cluster_')]

    for cluster_name in cluster_folders:
        cluster_path = os.path.join(clusters_path, cluster_name)
        image_files = [f for f in os.listdir(cluster_path) if f.endswith(('.jpg', '.jpeg'))]
        for image_file in image_files:
            data.append({
                'image_path': os.path.join(cluster_path, image_file),
                'cluster': cluster_name
            })

    df = pd.DataFrame(data)
    dataset = Dataset.from_pandas(df)
    return dataset

# Choose processing method
use_hf_dataset = False  # Set to True for large datasets

if use_hf_dataset:
    # Process using Hugging Face dataset
    dataset = create_hf_dataset(clusters_path)
    for example in tqdm(dataset, desc="Processing images"):
        image_path = example['image_path']
        cluster_name = example['cluster']
        try:
            image, original_shape = preprocess_image(image_path)
            mask = model.predict(np.expand_dims(image, axis=0), verbose=0)[0]
            if mask.shape[-1] > 1:
                mask = np.argmax(mask, axis=-1)
            else:
                mask = mask[..., 0]
            extract_panels(image_path, mask, original_shape, output_dir, cluster_name, example['index'])
        except Exception as e:
            print(f"Error processing {image_path}: {e}")
else:
    # Process directly
    process_images_directly(clusters_path, model, output_dir)

# Cell 3: Zip and save extracted panels to Google Drive
def zip_directory(directory, zip_path):
    with zipfile.ZipFile(zip_path, 'w', zipfile.ZIP_DEFLATED) as zipf:
        for root, _, files in os.walk(directory):
            for file in files:
                file_path = os.path.join(root, file)
                arcname = os.path.relpath(file_path, directory)
                zipf.write(file_path, os.path.join('extracted_panels', arcname))

# Create zip file
#zip_directory(output_dir, zip_output_path)
#print(f"Extracted panels saved to {output_dir}")
#print(f"Zipped panels saved to {zip_output_path}")

# Optional: Debug a sample prediction
sample_cluster = [f for f in os.listdir(clusters_path) if f.startswith('cluster_')][0]
sample_image = [f for f in os.listdir(os.path.join(clusters_path, sample_cluster)) if f.endswith(('.jpg', '.jpeg'))][0]
sample_image_path = os.path.join(clusters_path, sample_cluster, sample_image)
sample_image, original_shape = preprocess_image(sample_image_path)
sample_mask = model.predict(np.expand_dims(sample_image, axis=0), verbose=0)[0]
if sample_mask.shape[-1] > 1:
    sample_mask = np.argmax(sample_mask, axis=-1)
else:
    sample_mask = sample_mask[..., 0]
cv2.imwrite('/content/sample_pred_mask.png', sample_mask * 255)
print("Sample predicted mask saved to /content/sample_pred_mask.png")

In [ ]:
import os
import zipfile
import random
from pathlib import Path

#@markdown Create a numbered set for further clustering

# Define the root folder containing subfolders with images
root_folder = "/content/extracted_panels"
#/content/drive/MyDrive/extracted_panels"

# Generate a random 5-digit number
random_number = f"{random.randint(0, 99999):05d}"

# Define the output zip file path
zip_file_name = f"/content/drive/MyDrive/training_data_{random_number}.zip"

# Create a zip file
with zipfile.ZipFile(zip_file_name, 'w', zipfile.ZIP_DEFLATED) as zipf:
    # Walk through all subfolders in the root folder
    for subfolder in Path(root_folder).glob("cluster_*"):
        if subfolder.is_dir():
            # Iterate through all files in the subfolder
            for file_path in subfolder.glob("*"):
                if file_path.is_file() and file_path.suffix.lower() in ('.jpg', '.jpeg', '.png', '.bmp', '.gif'):
                    # Add the image to the zip file, preserving the subfolder structure
                    zipf.write(file_path, arcname=file_path.relative_to(root_folder))

print(f"Images zipped successfully into {zip_file_name}")


Go back to top of notebook and repeat clustering with panels to see results ⬆

#Training Deep Panel finetune for specific task

Train a Deep Panel Model

Refer to https://github.com/pedrovgs/DeepPanel  in how to build a dataset

In [ ]:
# Install required dependencies
!pip install tensorflow
!pip install opencv-python-headless
!pip install numpy
!pip install tqdm

# Clone the DeepPanel repository
!git clone https://github.com/pedrovgs/DeepPanel.git
%cd DeepPanel

# Import necessary libraries
import os
import zipfile
from google.colab import drive
import tensorflow as tf
import cv2
import numpy as np
from tqdm import tqdm

# Mount Google Drive
drive.mount('/content/drive')

# Unzip the dataset
dataset_path = '/content/drive/MyDrive/mia_panel_dataset.zip'
extract_path = '/content/mia_panel_dataset'

with zipfile.ZipFile(dataset_path, 'r') as zip_ref:
    zip_ref.extractall(extract_path)

# Remove __MACOSX folder if it exists
!rm -rf /content/mia_panel_dataset/__MACOSX

# Verify dataset structure
!ls /content/mia_panel_dataset
#!ls /content/mia_panel_dataset
# Verify number of files in training folders
!echo "Training raw images:"
!ls -l /content/mia_panel_dataset/training/raw | wc -l
!echo "Training masks:"
!ls -l /content/mia_panel_dataset/training/segmentation_mask | wc -l
# Verify subfolder structure (uncomment if needed for debugging)
# !ls /content/mia_panel_dataset/mia_panel_dataset/test
# !ls /content/mia_panel_dataset/mia_panel_dataset/training

# Create necessary directories for model checkpoints
os.makedirs('checkpoints', exist_ok=True)

# Define dataset paths (updated for nested mia_panel_dataset folder)
train_raw_path = '/content/mia_panel_dataset/training/raw'
train_mask_path = '/content/mia_panel_dataset/training/segmentation_mask'
test_raw_path = '/content/mia_panel_dataset/test/raw'
test_mask_path = '/content/mia_panel_dataset/test/segmentation_mask'

# Define configuration
class Config:
    INPUT_SHAPE = (256, 256, 3)  # Adjust based on your image size
    BATCH_SIZE = 5
    EPOCHS = 200
    LEARNING_RATE = 1e-4
    MODEL_PATH = 'checkpoints/model.keras'  # Updated to .keras format

# Custom data loader
def load_image_and_mask(image_path, mask_path, target_size):
    image = tf.io.read_file(image_path)
    image = tf.image.decode_png(image, channels=3)
    image = tf.image.resize(image, target_size[:2])
    image = image / 255.0  # Normalize to [0, 1]

    mask = tf.io.read_file(mask_path)
    mask = tf.image.decode_png(mask, channels=1)
    mask = tf.image.resize(mask, target_size[:2], method='nearest')
    mask = tf.cast(mask, tf.float32)
    # Normalize mask to [0, 1] for binary segmentation
    mask = mask / tf.reduce_max(mask)  # Ensure mask values are [0, 1]
    mask = tf.where(mask > 0.5, 1.0, 0.0)  # Binarize mask

    return image, mask

def create_dataset(raw_path, mask_path, batch_size, input_shape, is_train=True):
    image_files = sorted([os.path.join(raw_path, f) for f in os.listdir(raw_path) if f.endswith(('.png', '.jpg', '.jpeg'))])
    mask_files = sorted([os.path.join(mask_path, f) for f in os.listdir(mask_path) if f.endswith(('.png', '.jpg', '.jpeg'))])

    # Ensure matching pairs
    print(f"Found {len(image_files)} images and {len(mask_files)} masks")
    assert len(image_files) == len(mask_files), "Number of images and masks must match"
    assert len(image_files) > 0, "No images found in dataset"

    dataset = tf.data.Dataset.from_tensor_slices((image_files, mask_files))
    dataset = dataset.map(
        lambda x, y: load_image_and_mask(x, y, input_shape),
        num_parallel_calls=tf.data.AUTOTUNE
    )

    if is_train:
        dataset = dataset.shuffle(buffer_size=1000)

    dataset = dataset.batch(batch_size).prefetch(tf.data.AUTOTUNE)
    return dataset

# Create datasets
train_dataset = create_dataset(
    train_raw_path, train_mask_path, Config.BATCH_SIZE, Config.INPUT_SHAPE, is_train=True
)
test_dataset = create_dataset(
    test_raw_path, test_mask_path, Config.BATCH_SIZE, Config.INPUT_SHAPE, is_train=False
)

# Inspect a sample mask to verify format (optional debugging)
sample_image, sample_mask = next(iter(train_dataset))
print(f"Sample mask shape: {sample_mask.shape}, min: {tf.reduce_min(sample_mask)}, max: {tf.reduce_max(sample_mask)}")

# Define the model (simplified U-Net inspired by DeepPanel's segmentation goal)
def build_model(input_shape):
    inputs = tf.keras.Input(shape=input_shape)

    # Encoder
    c1 = tf.keras.layers.Conv2D(64, 3, padding='same', activation='relu')(inputs)
    c1 = tf.keras.layers.Conv2D(64, 3, padding='same', activation='relu')(c1)
    p1 = tf.keras.layers.MaxPooling2D()(c1)

    c2 = tf.keras.layers.Conv2D(128, 3, padding='same', activation='relu')(p1)
    c2 = tf.keras.layers.Conv2D(128, 3, padding='same', activation='relu')(c2)
    p2 = tf.keras.layers.MaxPooling2D()(c2)

    # Bottleneck
    b = tf.keras.layers.Conv2D(256, 3, padding='same', activation='relu')(p2)
    b = tf.keras.layers.Conv2D(256, 3, padding='same', activation='relu')(b)

    # Decoder
    u1 = tf.keras.layers.Conv2DTranspose(128, 2, strides=2, padding='same')(b)
    u1 = tf.keras.layers.Concatenate()([u1, c2])
    c3 = tf.keras.layers.Conv2D(128, 3, padding='same', activation='relu')(u1)
    c3 = tf.keras.layers.Conv2D(128, 3, padding='same', activation='relu')(c3)

    u2 = tf.keras.layers.Conv2DTranspose(64, 2, strides=2, padding='same')(c3)
    u2 = tf.keras.layers.Concatenate()([u2, c1])
    c4 = tf.keras.layers.Conv2D(64, 3, padding='same', activation='relu')(u2)
    c4 = tf.keras.layers.Conv2D(64, 3, padding='same', activation='relu')(c4)

    outputs = tf.keras.layers.Conv2D(1, 1, activation='sigmoid')(c4)  # Binary segmentation
    model = tf.keras.Model(inputs, outputs)
    return model

# Build and compile model
model = build_model(Config.INPUT_SHAPE)
model.compile(
    optimizer=tf.keras.optimizers.Adam(learning_rate=Config.LEARNING_RATE),
    loss='binary_crossentropy',  # Adjust if masks are multi-class
    metrics=['accuracy']
)

# Train the model
history = model.fit(
    train_dataset,
    validation_data=test_dataset,
    epochs=Config.EPOCHS,
    callbacks=[
        tf.keras.callbacks.ModelCheckpoint(
            Config.MODEL_PATH, save_best_only=True, monitor='val_loss'
        )
    ]
)

# Save the trained model to Google Drive
!cp checkpoints/model.keras /content/drive/MyDrive/deeppanel_model.keras